# Processing Issues using Gemma7b

In [1]:
import ollama
import json
import tiktoken
from llama_index.core.node_parser import TokenTextSplitter
from functools import partial

In [2]:
with open('data/prediction_data/issues.json') as f:
    issues_data = [json.loads(line) for line in f]
#issues_data

### Text Processor

In [3]:
chunk_size = 6000
separator = '\n'
backup_separators = [".", " "]
tokenizer = partial(tiktoken.get_encoding("cl100k_base").encode, allowed_special="all")

def txt_splitter(text):
    text_splitter = TokenTextSplitter(separator=separator,
                                        chunk_size=chunk_size,
                                        backup_separators=backup_separators,
                                        tokenizer=tokenizer)
    # print(len(tokenizer(text))))  ### Check token size 
    if len(tokenizer(text)) <= chunk_size:
        return [text]
    
    chunks = text_splitter.split_text(text)
    return chunks

### Prepare Issues

In [4]:
for issues in issues_data:
    issues['issues'] = txt_splitter(issues['issues'])

## LLM Magic

Prompt Templates

In [5]:
def generate_summary_template(context, prev_summary=''):

    prompt_template = f"""
    You are a Singapore Lawyer. \n
    summarise the main issues of the legal judgment below in 1500 words:\n
    {prev_summary}\n
    {context}.
    """
    return prompt_template

def generate_final_template(context):
    prompt_template = f"""
    {context}.\n
    summarise the legal issues above into sentences separated by full-stop. DO NOT give any headers.

    EXAMPLE: (if there are 3 issues)
    Issue 1. Issue 2. Issue 3.
    """
    return prompt_template

Start

In [6]:
json_path = 'processed_issues.json'

In [7]:
checkpoint = 0
for issues in issues_data:
    if len(issues) == 3:
        continue
    
    prev_summary = ''
    checkpoint += 1
    for chunk in issues['issues']:
        context = generate_summary_template(chunk, prev_summary)
        response = ollama.generate(model='gemma', prompt=str(context), stream=False)
        prev_summary = response['response']
    
    print(prev_summary)
    overall_summary = generate_final_template(prev_summary)
    response = ollama.generate(model='gemma', prompt=str(overall_summary), stream=False)
    final_summary = response['response']
    
    issues['summarised issues'] = final_summary.split('.')

    
    if checkpoint == 500:
        with open(json_path, 'w') as jf:
            json.dump(issues_data, jf, indent=4)
        checkpoint = 0

## Main Issues of the Legal Judgment:

**1. Joinder of Additional Party:**

- The court questioned whether the additional party should have been included in the initial action.
- The reasoning suggests that joining the party at that stage was not necessary for a fair trial.
- The judgment emphasizes that failing to join a potential defendant in an earlier case does not automatically bar them from being sued in subsequent proceedings.

**2. Abuse of Court Process:**

- The appellant argued that they could not have raised a specific claim in the previous action due to an alleged mistake of law.
- The court accepted this argument, concluding that the claim wasn't fraudulently withheld.
- The judgment clarifies that discovering an error after litigation concludes doesn't automatically justify an abuse of process.

**3. Recover of Sum Paid Under Mistake:**

- The court recognized the appellant's right to recover the sum allegedly paid under a legal misconception.
- This right applies even i

In [8]:
for issues in issues_data:
    print(issues['summarised issues'])

['The legal issues are:\n\nJoinder of an additional party was not necessary for a fair trial at the initial action stage', ' Failing to join a potential defendant in an earlier case does not automatically bar them from being sued in subsequent proceedings', " The appellant can recover the sum allegedly paid under a legal misconception, even if the mistake wasn't discovered until after the previous case concluded", ' The court balanced the interests of preventing frivolous litigation with facilitating access to justice', ' Procedural fairness requires allowing the defendant to respond to the claim in the current action', '']
['The provided text is not included in the prompt, so I am unable to summarise the legal issues', '']
['Calculation of damages was disputed, with the appellants arguing for a 15% rate instead of the 16', '1% set by the trial judge', ' The court upheld the 16', '1% calculation', ' The appellants claimed that Clause 8 of the Rochas agreement had been varied, but the c